<h1> Introductory Python Notebook to Semantic Shift Analysis Guide </h1>

The purpose of this guide is to understand how parts of the Semantic Shift Api works

<h3> Guidelines of this notebook </h3>

<p><b> Module functions </b></p>
The goal of this notebook is to introduce a user to the module functions, hence descriptions surround how they work and how they should be used.

<p><b> Notebook functions </b></p>
These functions are helper functions that are implemented <i>specficially</i> for this notebook to illustrate certain examples in a clean manner. The user should not necessarily pay attention to them, and should only study them in detail if one is confused about the functionality that is being demonstrated or described.

In [2]:
import pandas as pd
import numpy as np
import gzip
import json
import os, glob, sys
import multiprocessing as mp

<h3> Module Imports </h3>
We append module_path to sys.path to be able to import any inhouse module.<br>

In [6]:
module_path = '/home/ndg/users/abhand1/subreddit_data/module/'
if module_path not in sys.path:
    sys.path.append(module_path)

Load relevant modules for Slang Analysis. 

<ul>
    <li>Slang Analyser - Computes Affinity terms for subreddits</li>
    <li>Subreddinfo - Contains helper functions for such as pickle_dump, and pickle_load</li>
    <li>Config - Loads path information. Path information is prefixed in config. </li>
    <li>Original Subreddit Metrics - The engine that computes </li>
</ul>

In [137]:
import slang_analyser
from subreddinfo import pickle_dump, pickle_load
import config

import original_subreddit_metrics

<h3> Loading Subreddits </h3> <br>
Below, we calculate and load the subreddits in a list for the interval of 2014 November to 2015 June.<br>
The function get_subnames loads and parses subreddits from a file that contains subreddits line by line. 

In [15]:
def get_subnames(fname):
    """Gets Subnames from a local file."""
    subnames = []
    with open(fname) as f:
        subnames = f.read().split('\n')[:-1]
    return subnames

all_subs_path = 'all_subreddits_above_10000_comments.txt'
all_subs_full_path = os.path.join(module_path, all_subs_path)
subnames = get_subnames(all_subs_full_path)

In this introductory notebook guide, we will be using the first 10 subreddits in the subname category to demonstrate the features and capacity of the modules that we have. These subreddits are:

<p>['motogp',
 'italy',
 'Shave_Bazaar',
 'poker',
 'ableton',
 'batman',
 'havoc_bot',
 'ftlgame',
 'lootcrate',
 'lacrosse']</p>

In [140]:
demo_subs = subnames[:10]

<h3> Calculating Affinity Values </h3> <br>
The first set of features displayed is the way to extract affinity terms for a subreddit. A pre-requisite for this is to compute word-freq dictionaries for each subreddit that maps word to its frequency {word -> freq}. This step is done, and these dictionaries are store in config.SUBDIR_ANALYSIS_LOAD_PATH/subname/{subname + "\_filtered_lemma.pkl"} 



The affinity terms are computed by passing the list of subnames to slang_analyser.run_slang_analyser which internally calls a function called affinity_analysis. <br>
affinity_analysis computes affinity terms for each subreddit using the affinity analysis formula. <br>

The affinity value for each term will be dependent on the number of subreddits and type of subreddits that are passed to the function, because the values are dependent on the pool of data available.

In [143]:
demo_affinity_terms = slang_analyser.run_slang_analyser(demo_subs)

In [199]:
def extract_some_affinity_terms(list_affinity_terms, subs, sub_index, head=10, desc=True, show_aff_score=True):
    """A print function that displays a head number of affinity terms for a subreddit.
    
    Args:
        list_affinity_terms (list): a list of affinity terms (dictionary). Maps aff -> aff score.
        
    Returns:
        smth
    
    """
    print("Printing {} affinity terms of {}".format(head, subs[sub_index]))
    target_affinity_dic = list_affinity_terms[sub_index]
    aff_head = sorted(target_affinity_dic, 
                      key=lambda x: target_affinity_dic[x], 
                      reverse=desc)[:head]
    
    if show_aff_score:
        print(*list((aff, target_affinity_dic[aff]) for aff in aff_head), sep='\n')


In [198]:
extract_some_affinity_terms(demo_affinity_terms, demo_subs, 0)

Printing 10 affinity terms of motogp
('lap', 0.9991460290350128)
('marc', 0.9989561586638831)
('marquez', 0.9987266079763581)
('motogp', 0.9983514955863898)
('rid', 0.9983221476510067)
('honda', 0.9980065686539601)
('pedrosa', 0.997907949790795)
('dovi', 0.9977426636568849)
('cal', 0.9975728155339806)
('ducati', 0.997542539388946)


<h3> Graphing Imports </h3>
These imports are useful for the purposes of graphing

In [800]:
# Standard plotly imports
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

"""
For linear regrssion
"""
from sklearn import linear_model

<h2> Helper Functions for Numerical Analysis and Plotting </h2> 

In [793]:
home_dir = '/home/ndg/users/abhand1/'
all_subs_df = pickle_load(home_dir + 'all_subreddits_df.pkl')
all_subs_df_30 = all_subs_df[all_subs_df['aff_wc_in_models'] > 30]

For the purposes of accuracy, while we have datasets of about 2500+ subreddits, we  only accept subreddits where 
of the 100 affinity terms, over 30 were present in the word embeddings of all time intervals (many happen to be not present in all 4). 30 is the threshold, and we end up with about 1400+ subreddits. 

<b>Note:</b> Now we store in the folder <i>slang_semantic_shift_df</i> dataframess which have n number of affinity terms present in all four word embeddings. all_subs_df does not reflect this data, whereas it contains the results of the top 100 absolute affinity terms (regardless of if they are present in all 4 embeddings).

Also: <br>
aff_wc_in_models -> the number of words present in all four word embeddings (out of the top n affinity terms) <br>
wc -> word count

In [796]:
# Data that is important
top_100_aff_df = pd.read_csv(home_dir + 'slang_semantic_shift_df/top_100_aff.csv', index_col=0)
top_50_aff_df = pd.read_csv(home_dir + 'slang_semantic_shift_df/top_50_aff.csv', index_col=0)
bot_50_aff_df = pd.read_csv(home_dir + 'slang_semantic_shift_df/bottom_50_aff.csv', index_col=0)

<h3> Explanation of columns </h3>
Only explaining important columns. <br>
Ignore these columns: mean,	std, slang_to_user_wc, user_percent, average_affinity_value <br>
half_load_average: Average affinity values of 

In [797]:
top_50_aff_df.head()

mean       std  slang_to_user_wc  user_percent  \
motogp        0.288  1.020322               169      0.130790   
italy         0.096  0.585478                86      0.019293   
Shave_Bazaar  0.340  1.276088               200      0.241993   
poker         2.041  6.611302               462      0.238101   
ableton       0.416  1.650740               199      0.153392   

              average_affinity_value  forward_shift  backward_shift  \
motogp                      0.106694          0.152           0.206   
italy                       0.997124          0.514           0.544   
Shave_Bazaar                0.050463          0.234           0.130   
poker                       0.129063          0.402           0.404   
ableton                     0.034866          0.190           0.198   

              net_forward_shift  net_backward_shift  aff_wc_in_models  \
motogp                    0.008               0.046                50   
italy                    -0.002               0.032                50   
Shave_Bazaar             -0.098              -0.006                50   
poker                    -0.018               0.020                50   
ableton                   0.002               0.006                50   

              half_load_affinity_average   loyalty  dedication  no._of_users  \
motogp                          0.702799  0.076748    0.173479          2202   
italy                           0.999672  0.227693    0.275121          4976   
Shave_Bazaar                    0.196970  0.056940    0.218505          1405   
poker                           0.986001  0.135908    0.217452          8572   
ableton                         0.121612  0.044617    0.092920          2712   

              no._of_comments  
motogp                  24799  
italy                  183884  
Shave_Bazaar            14866  
poker                  138814  
ableton                 11703

The following set of function help with finding a moving average (for smoothing purposes).

More information: 
http://bestmaths.net/online/index.php/year-levels/year-12/year-12-topic-list/smoothing-techniques/

In [370]:
def get_smoothened_intervaled_frames(temp, sorting_index, n=10, asc=False):
    """
    Purpose: 
    The following function receives a dataframe, which it treats it as temporary, and then sorts the dataframe
    based on the column which is indexed. For instance, if the sorting index is 'loyalty', then it will
    sort the rows in order of loyalty. The function, then smoothens the dataset by binning it in boxes
    of size n (default is 10). In other words, n consecutive rows are averaged and smoothened into a new row,
    and this collection of smoothened rows is returned as a new dataframe.
    """
    temp = temp.sort_values(by=sorting_index)
    i = 0
    df_val = 0
    new_temp = pd.DataFrame(columns=temp.columns)
    temp_summer = 0
    for index, row in temp.iterrows():
        if i % n == 0 and i != 0:
            temp_summer = temp_summer/n
            new_temp.loc[df_val] = temp_summer
            df_val += 1
            temp_summer = 0
            i = 0
        if type(temp_summer) == int and temp_summer == 0:
            temp_summer = row
        else:
            temp_summer += row
        i += 1
    temp_summer = temp_summer/i
    new_temp.loc[df_val] = temp_summer
    return new_temp.iloc[:-1]
    

The following set of helper functions help with plotting the dataframe data.
It produces an interactive plotly graph

In [792]:
def data_to_plotly(x):
    k = []
    
    for i in range(0, len(x)):
        k.append(x[i][0])
        
    return k


def create_iplot_trends(df, x_index, y_indexes, markers={'reg': 'lines', 'index': 'markers'}, title='', secondary_y=''):
    temp_df = df.copy()
    df_markers = {}
    keys = []
    for y_index in y_indexes:
        regr = linear_model.LinearRegression()
        x_val = np.reshape(list(df[x_index]), (-1, 1))
        y_val = np.reshape(list(df[y_index]), (-1, 1))
        df_markers[y_index] = markers['index']
        keys.append(y_index)
        regr.fit(x_val, y_val)
        
        y_reg = regr.predict(x_val)
        y_reg_index = y_index + '_reg'
        temp_df[y_reg_index] = data_to_plotly(y_reg)
        df_markers[y_reg_index] = markers['reg']
        keys.append(y_reg_index)
    temp_df_sorted = temp_df.set_index(x_index).sort_index()
    temp_df_sorted.iplot(keys=keys, mode=df_markers, xTitle=x_index, title=title, secondary_y=secondary_y)
        

<h2> Numerical Analysis</h2>

In the following examples of numerical analysis, we run analysis on smoothened datasets. In other_words, a group of n consecutive points are averaged (default n = 10), and made into one point for all points. At times all points instead of moving (or smoothing) averages are used. This is to illustrate if the trend exists on a non-smoothened surface. 

For instance, Loyalty and Semantic values do not have a clear relationship when running the analysis on loyalty vs. semantic shift, Hence the loss of information with smoothing  may lead one  to believe that there may be a trend.

<b>Sorting Reason:</b> For each primary variable whose relationship is being compared against other features, we create a smoothened dataframe from the complete dataframe SORTED on the primary variable. This allows us to to see if linear patterns are present.

<b>ALSO NOTE </b>: "Semantic Shift" and "Net Semantic Shift" are <b>not</b> the same.
Net semantic shift defines the amount of net shift words have had

<h3> Analysis of relationship of Loyalty with Existing Features </h3>
Explore the relationship between loyalty and semantic shift, net semantic shift, no._of_comments and no._of_users

In [479]:
"""
This dataframe basically means that we are smoothening it by binning n points to 1, 
since the dataframe contains 1400+/2500+ points.

default n = 10
"""

loyalty_smoothened_df = get_smoothened_intervaled_frames(ss, 'loyalty')

loyalty_smoothened_df_10 = get_smoothened_intervaled_frames(ss, 'loyalty', n=200)

In [714]:
# Plotting all 474 points. 
create_iplot_trends(df=filter_stuff[filter_stuff['net_backward_shift']  >  0.1], 
                       x_index='half_load_affinity_average', 
                       y_indexes=['no._of_comments', 'net_backward_shift', 'loyalty'], 
                       title='Loyalty Vs. Net Semantic Shift', secondary_y='net_backward_shift')

In [763]:
new_df.columns

Index(['mean', 'std', 'slang_to_user_wc', 'user_percent',
       'average_affinity_value', 'forward_shift', 'backward_shift',
       'net_forward_shift', 'net_backward_shift', 'aff_wc_in_models',
       'half_load_affinity_average', 'loyalty', 'dedication', 'no._of_users',
       'no._of_comments', 'net_forward_shift_neutral',
       'net_backward_shift_neutral', 'backward_shift_diff'],
      dtype='object')

In [775]:
os.listdir('/home/ndg/users/carmst16')

PermissionError: [Errno 13] Permission denied: '/home/ndg/users/carmst16'

In [777]:
ss[ss['backward_shift'] == 0]

mean       std  slang_to_user_wc  user_percent  \
announcements  1.495  4.895506               365      0.091465   
DWMA           0.018  0.132951                21      0.333333   
empirepowers   0.046  0.240591                50      0.511111   

               average_affinity_value  forward_shift  backward_shift  \
announcements                0.040756            0.0             0.0   
DWMA                         0.049139            0.0             0.0   
empirepowers                 0.094016            0.0             0.0   

               net_forward_shift  net_backward_shift  aff_wc_in_models  \
announcements                0.0                 0.0                 0   
DWMA                         0.0                 0.0                 0   
empirepowers                 0.0                 0.0                 0   

               half_load_affinity_average   loyalty  dedication  no._of_users  \
announcements                         0.0  0.000061    0.036035         16345   
DWMA                                  0.0  0.333333    0.666667            54   
empirepowers                          0.0  0.044444    0.711111            90   

               no._of_comments  
announcements            46339  
DWMA                     23049  
empirepowers             10815

In [772]:
os.listdir('slang_semantic_shift_df/')

['top_100_aff.csv', 'bottom_50_aff.csv', 'top_50_aff.csv']

In [804]:
# Plotting all 474 points. 
create_iplot_trends(df=ss, 
                       x_index='net_backward_shift', 
                       y_indexes=['half_load_affinity_average'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [767]:
# Plotting all 474 points. 
create_iplot_trends(df=new_df, 
                       x_index='loyalty', 
                       y_indexes=['backward_shift_diff'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [790]:
# Plotting all 474 points. 
create_iplot_trends(df=new_df, 
                       x_index='loyalty', 
                       y_indexes=['net_backward_shift', 'net_backward_shift_neutral'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [716]:
# Plotting all 474 points. 
create_iplot_trends(df=ss2, 
                       x_index='loyalty', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [573]:
filter_stuff[filter_stuff['net_backward_shift'] > 0.2]

mean        std  slang_to_user_wc  user_percent  \
DFO                  0.767   2.509325               280      0.143741   
fantasybaseball      1.018   3.036392               328      0.134443   
MaddenMobileForums   0.672   2.135045               295      0.243478   
amiibo               7.114  17.329368               693      0.218288   
CitiesSkylines       3.220  10.445363               465      0.098024   
ContestOfChampions   0.425   1.945347               205      0.227030   
Nationals            0.398   1.384773               221      0.178796   
bloodborne           4.765  12.531870               590      0.157427   
Muse                 0.852   2.869860               317      0.181663   
StarWarsLeaks        0.540   1.993590               224      0.214626   
GrandTheftAutoV_PC   3.948  10.668894               498      0.144737   
AgMarketplace        2.717  12.812373               504      0.280972   
battlecats           0.515   1.991927               232      0.249395   
EvolveGame           1.922   5.057461               430      0.157348   
1200isplenty         0.748   1.930931               311      0.146351   
killingfloor         0.702   2.218377               267      0.117274   
kancolle             0.180   0.735935               123      0.137510   
h1z1                 7.071  16.752551               624      0.188009   
linuxmasterrace      0.294   1.245618               152      0.082330   
stevenuniverse       1.827   4.766033               436      0.178767   
LightNovels          0.484   1.594285               225      0.135233   
Neverwinter          0.612   1.754268               259      0.142326   
gameofthrones       11.043  30.660351               723      0.121886   
BlackPeopleTwitter  17.389  36.629601               848      0.212170   
ttcafterloss         0.056   0.294727                61      0.202899   
PrettyLittleLiars    1.320   3.939239               414      0.294840   
MonsterHunter        3.444   9.884779               561      0.129202   
BF_Hardline          1.463   4.478463               367      0.169153   
MortalKombat         2.460   6.185014               486      0.187286   

                    average_affinity_value  forward_shift  backward_shift  \
DFO                               0.114808          0.129           0.546   
fantasybaseball                   0.093264          0.141           0.444   
MaddenMobileForums                0.064200          0.161           0.392   
amiibo                            0.034992          0.403           0.589   
CitiesSkylines                    0.040380          0.157           0.500   
ContestOfChampions                0.036912          0.213           0.444   
Nationals                         0.108194          0.119           0.321   
bloodborne                        0.086970          0.146           0.576   
Muse                              0.067352          0.203           0.457   
StarWarsLeaks                     0.074880          0.198           0.396   
GrandTheftAutoV_PC                0.024867          0.155           0.519   
AgMarketplace                     0.104647          0.179           0.399   
battlecats                        0.148786          0.198           0.435   
EvolveGame                        0.030757          0.217           0.416   
1200isplenty                      0.039016          0.152           0.373   
killingfloor                      0.069531          0.163           0.433   
kancolle                          0.193740          0.127           0.475   
h1z1                              0.022714          0.232           0.502   
linuxmasterrace                   0.041403          0.202           0.380   
stevenuniverse                    0.081901          0.163           0.454   
LightNovels                       0.196393          0.159           0.366   
Neverwinter                       0.094629          0.208           0.440   
gameofthrones                     0.088802          0.218   

In [717]:
# Plotting all 474 points. 
create_iplot_trends(df=filter_stuff, 
                       x_index='loyalty', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [ ]:
#ratio of loyalty vs subreddit size -> 

In [718]:
# Plotting all 474 points. 
create_iplot_trends(df=loyalty_smoothened_df_10, 
                       x_index='loyalty', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [719]:
# Plotting all 474 points. 
create_iplot_trends(df=loyalty_smoothened_df_10, 
                       x_index='loyalty', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='Loyalty Vs. Net Semantic Shift')

In [721]:
# CLEARLY No Distinguishable relationship!! Plotting 47 points.
# Plotting all 474 points. 
create_iplot_trends(df=ss, 
                       x_index='loyalty', 
                       y_indexes=['backward_shift', 'forward_shift'], 
                       title='Loyalty Vs. Semantic Shift')

In [743]:
jj = filter_stuff.copy()
jj['smth'] = filter_stuff['backward_shift'] - filter_stuff['forward_shift']

In [744]:
lk = get_smoothened_intervaled_frames(jj, 'smth')

In [748]:
len(jj)

1744

In [749]:
len(jj[jj['smth'] > 0])

1094

In [751]:
# CLEARLY No Distinguishable relationship!!
create_iplot_trends(df=jj, 
                       x_index='loyalty', 
                       y_indexes=['smth'], 
                       title='Loyalty Vs. Semantic Shift')

In [722]:
# CLEARLY No Distinguishable relationship!!
create_iplot_trends(df=loyalty_smoothened_df_10, 
                       x_index='loyalty', 
                       y_indexes=['backward_shift', 'forward_shift'], 
                       title='Loyalty Vs. Semantic Shift')

In [469]:

all_subs_df[['no._of_users', 'no._of_comments', 'loyalty']].set_index('loyalty').sort_index().iplot(subplots=True, subplot_titles=True, mode='markers', xTitle='loyalty')



<h3> Analysis of relationship of No. Of Comments with Existing Features </h3>
Explore the relationship between no. of comments and semantic shift, net semantic shift, and loyalty

In [486]:
ss[ss['no._of_comments'] > 20000]

1794

In [487]:
create_iplot_trends(df=ss[ss['no._of_comments'] > 20000], 
                       x_index='no._of_comments', 
                       y_indexes=['backward_shift', 'forward_shift'], 
                       title='No. of Comments Vs. Semantic Value')


In [482]:
"""
This dataframe basically means that we are smoothening it by binning n points to 1, 
since the dataframe contains 1400+/2500+ points.

default n = 10
"""

comments_smoothened_df = get_smoothened_intervaled_frames(ss, 'no._of_comments')

comments_smoothened_df_10 = get_smoothened_intervaled_frames(ss, 'no._of_comments', n=200)

In [492]:
create_iplot_trends(df=ss[ss['no._of_comments'] > 20000], 
                       x_index='no._of_comments', 
                       y_indexes=['net_backward_shift'], 
                       title='No. of Comments Vs. Semantic Value')


In [757]:
create_iplot_trends(df=comments_smoothened_df_10, 
                       x_index='no._of_comments', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='No. of Comments Vs. Semantic Value')


In [756]:
create_iplot_trends(df=ss, 
                       x_index='no._of_comments', 
                       y_indexes=['net_backward_shift', 'net_forward_shift'], 
                       title='No. of Comments Vs. Semantic Value')


In [607]:
bytea = ss2['forward_shift'] != 0 
byteb = ss2['no._of_comments'] > 20000
bytec = ss2['aff_wc_in_models'] == 50
filter_stuff2 = ss2[bytea & byteb & bytec]

In [525]:
bytea = ss['forward_shift'] != 0 
byteb = ss['no._of_comments'] > 20000
bytec = ss['aff_wc_in_models'] == 100
filter_stuff = ss[bytea & byteb & bytec]

In [ ]:
ss[ss['no._of_comments'] > 20000]

In [521]:
filter_stuff.sort_values(by="half_load_affinity_average")['loyalty']

gif                     0.002571
answers                 0.001825
rant                    0.008303
promos                  0.004662
self                    0.005579
Damnthatsinteresting    0.001043
TrueAskReddit           0.002017
makemychoice            0.014096
AMA                     0.014140
geek                    0.000482
NoStupidQuestions       0.009902
instant_regret          0.000608
offmychest              0.019908
wallpapers              0.005051
firstworldproblems      0.001526
inthenews               0.003026
AskTrollX               0.024873
Foodforthought          0.003272
Frozenfriends           0.182065
interestingasfuck       0.002827
me_irl                  0.009705
explainlikeimfive       0.006096
entertainment           0.002716
blog                    0.000403
TrueReddit              0.007566
CasualConversation      0.064340
firstimpression         0.018227
fffffffuuuuuuuuuuuu     0.012427
Showerthoughts          0.007832
Advice                  0.023918
          

In [531]:
smth = get_smoothened_intervaled_frames(ss, 'loyalty')

In [566]:
jj = ss.rolling(window=50)

In [564]:
jj.mean().iloc[4:]

mean       std  slang_to_user_wc  user_percent  \
ableton                NaN       NaN               NaN           NaN   
batman                 NaN       NaN               NaN           NaN   
havoc_bot              NaN       NaN               NaN           NaN   
ftlgame                NaN       NaN               NaN           NaN   
lootcrate              NaN       NaN               NaN           NaN   
lacrosse            0.8601  3.086869             241.9      0.175130   
aliens              0.8498  3.049549             239.5      0.171251   
ruby                0.8677  3.119585             244.6      0.178650   
Everton             0.8594  3.092224             239.2      0.172460   
StarWars            1.4978  4.769341             256.9      0.165205   
Animewallpaper      1.5432  4.971624             266.5      0.184131   
HomeworkHelp        1.2492  4.215970             232.9      0.172141   
DFO                 1.3223  4.416832             258.1      0.172981   
Brogress            1.3623  4.510095             268.1      0.189066   
DarkSouls2          1.6050  5.275340             292.4      0.181465   
geology             1.5754  5.067043             284.9      0.163356   
mtgfinance          1.5805  5.112344             285.2      0.164311   
NHLHUT              1.6624  5.277855             310.4      0.177855   
berlin              1.6625  5.349870             306.2      0.170166   
GameDeals           1.2371  4.198533             294.5      0.164058   
crochet             1.3157  4.292324             307.2      0.150942   
community           1.4588  4.555906             331.9      0.154911   
cocktails           1.4201  4.429618             324.7      0.149957   
GoneWildPlus        1.6475  5.019764             342.1      0.148590   
perktv              1.3994  4.322279             316.0      0.151948   
Gaming4Gamers       1.4333  4.258056             329.8      0.153519   
Knife_Swap          1.4383  4.279731             331.7      0.167197   
perth               1.3579  4.121280             307.4      0.152953   
Predators           1.3611  4.050205             313.9      0.165113   
yorku               0.9566  2.977405             268.7      0.165210   
...                    ...       ...               ...           ...   
AntiPOZi            0.8660  2.948398             253.5      0.148873   
Huskers             0.8422  2.906962             245.2      0.142641   
oblivion            0.6236  1.995228             218.7      0.132049   
philosophy          0.6402  2.038861             224.7      0.124846   
Lollapalooza        0.6483  2.041329             226.1      0.139327   
NewOrleans          0.6664  2.218621             236.3      0.134058   
HeroesandGenerals   0.6614  2.150638             235.0      0.134177   
progressive         0.6692  2.176992             234.0      0.136605   
spicy               0.6794  2.186955             238.8      0.136715   
ukulele             0.4393  1.669883             206.1      0.147804   
EA_NHL              0.4658  1.763573             213.3      0.147481   
humor               0.5065  1.795816             227.9      0.133904   
AdvancedRunning     0.5054  1.880959             225.3      0.144631   
PolishGauntlet      0.4115  1.569908             204.0      0.181439   
badtattoos          0.5745  1.885426             228.5      0.188742   
wallpapers          0.7289  2.260686             243.3      0.187832   
OpTicGaming         0.7950  2.473163             261.9      0.195919   
AdoptMyVillager     0.8892  2.710870             284.8      0.226456   
timbers             0.8600  2.629402             272.7      0.232264   
mazda               0.8487  2.587953             270.3      0.224386   
circlejerk          1.3603  3.933954             303.9      0.219824   
SimCity             1.3311  3.869560             297.4      0.223114   
Disney_Infinity     1.3374  3.856186             300.8      0.231709   
pakistan            1.3417  3.893095             299.6      0.

In [571]:
create_iplot_trends(df=ss, 
                       x_index='half_load_affinity_average', 
                       y_indexes=['no._of_users'], 
                       title='No. of Comments Vs. Semantic Value')


In [649]:
slang_analyser = reload(slang_analyser)

In [650]:
original_subreddit_metrics = reload(original_subreddit_metrics)

In [645]:
os.listdir(os.path.join(config.SUBDIR_ANALYSIS_LOAD_PATH, 'nba'))

['nba_filtered_lemma.pkl',
 'nba_usernames.pkl',
 'nba_neutral_1000.pkl',
 'nba_u2w.pkl',
 'nba-2015-05-06.model',
 'nba_lemma_dic.pkl',
 'nba-2015-03-04.model',
 'nba_w2u.pkl',
 'nba-2015-01-02.model',
 'nba-2014-11-12.model',
 'nba_affinity_terms.pkl',
 'nba_aff_1000.pkl']

In [781]:
mm = sorted(stuff, key=lambda x: stuff[x], reverse=False)

In [785]:
mm = [m for m in mm if stuff[m] != 0]

In [787]:
mm[-100:]

['sheed',
 'delly',
 'iguodala',
 'peja',
 'yao',
 'boozer',
 'speights',
 'ginobli',
 'garnett',
 'coty',
 'grantland',
 'westbrook',
 'bibby',
 'kareem',
 'dwade',
 'cavs',
 'wilt',
 'rasheed',
 'kerr',
 'dray',
 'lebrons',
 'bynum',
 'bogut',
 'sacre',
 'blatt',
 'flagrant',
 'klay',
 'mutombo',
 'linsanity',
 'speight',
 'windhorst',
 'roty',
 'kyrie',
 'kobe',
 'ezeli',
 'ewing',
 'vogel',
 'telfair',
 'dunker',
 'halfcourt',
 'sabonis',
 'hakeem',
 'lebron',
 'freethrow',
 'divac',
 'mjax',
 'shaq',
 'mosgov',
 'kwame',
 'dellavedova',
 'rodman',
 'iverson',
 'hardens',
 'woj',
 'scottie',
 'dpoy',
 'olajuwon',
 'ecf',
 'battier',
 'varejao',
 'igoudala',
 'artest',
 'lbj',
 'ppg',
 'stepback',
 'beno',
 'horry',
 'lac',
 'delonte',
 'hubie',
 'shaqtin',
 'thabeet',
 'mcgrady',
 'gsw',
 'fta',
 'pippen',
 'lal',
 'bbiq',
 'nop',
 'fga',
 'wcf',
 'wnba',
 'fiba',
 'jvg',
 'drtg',
 'aau',
 'zbo',
 'fts',
 'mle',
 'joerger',
 'ortg',
 'fmvp',
 'probasketballtalk',
 'mip',
 'moy',
 '

In [786]:
mm[:100]

['map',
 'automoderator',
 'moderator',
 'cat',
 'compose',
 'bot',
 'recommend',
 'government',
 'mail',
 'download',
 'store',
 'email',
 'steam',
 'message',
 'service',
 'album',
 'driver',
 'automatically',
 'artist',
 'technology',
 'advice',
 'card',
 'comic',
 'enemy',
 'bottle',
 'her',
 'character',
 'author',
 'helpful',
 'online',
 'computer',
 'app',
 'photo',
 'shop',
 'car',
 'industry',
 'mission',
 'episode',
 'band',
 'damage',
 'meat',
 'update',
 'policy',
 'image',
 'filter',
 'craft',
 'gender',
 'location',
 'truck',
 'input',
 'search',
 'program',
 'society',
 'she',
 'station',
 'weapon',
 'information',
 'remove',
 'chat',
 'subject',
 'partner',
 'access',
 'method',
 'wheel',
 'copy',
 'function',
 'sexual',
 'user',
 'water',
 'student',
 'private',
 'request',
 'mine',
 'boot',
 'subreddit',
 'sale',
 'food',
 'community',
 'safety',
 'religion',
 'porn',
 'audio',
 'company',
 'info',
 'plant',
 'cell',
 'political',
 'female',
 'button',
 'iron',
 'sexy

In [651]:
%%time 
start = time()
ss3 = original_subreddit_metrics.generate_subreddit_metrics_df(subnames, n=1000, j=50, load_style="half_load")
end = time()

/home/ndg/users/abhand1/env3/lib/python3.5/site-packages/numpy/core/fromnumeric.py:3118: RuntimeWarning:

Mean of empty slice.

/home/ndg/users/abhand1/env3/lib/python3.5/site-packages/numpy/core/_methods.py:85: RuntimeWarning:

invalid value encountered in double_scalars



CPU times: user 47.3 s, sys: 24.6 s, total: 1min 11s
Wall time: 7min 11s


In [457]:
ss2

mean        std  slang_to_user_wc  user_percent  \
motogp              0.288   1.020322               169      0.130790   
italy               0.096   0.585478                86      0.019293   
Shave_Bazaar        0.340   1.276088               200      0.241993   
poker               2.041   6.611302               462      0.238101   
ableton             0.416   1.650740               199      0.153392   
batman              3.498  10.232106               550      0.196429   
havoc_bot           0.036   0.500704                28      0.135338   
ftlgame             0.610   2.256081               246      0.157257   
lootcrate           0.620   1.737700               260      0.207636   
lacrosse            0.656   4.998166               219      0.271074   
aliens              0.185   0.647128               145      0.091994   
ruby                0.275   1.285836               137      0.093284   
Everton             0.257   1.002472               146      0.180098   
StarWars            8.425  23.382480               639      0.165550   
Animewallpaper      0.870   3.673568               295      0.342655   
HomeworkHelp        0.558   2.675563               214      0.076522   
DFO                 0.767   2.509325               280      0.143741   
Brogress            1.010   3.188714               346      0.318110   
DarkSouls2          3.047   9.390143               503      0.131626   
geology             0.360   2.915202               144      0.089978   
mtgfinance          0.236   1.100138               148      0.101549   
NHLHUT              1.094   2.940946               389      0.228727   
berlin              0.258   1.722625               104      0.103200   
GameDeals           4.171  11.869109               522      0.104471   
crochet             1.656   4.611471               422      0.211494   
community           1.989   5.311391               461      0.116214   
cocktails           0.380   1.246435               208      0.094199   
GoneWildPlus        3.284   9.090178               520      0.304441   
perktv              0.566   2.415294               242      0.165207   
Gaming4Gamers       0.699   2.272971               282      0.105685   
...                   ...        ...               ...           ...   
AntiPOZi            0.238   0.871410               146      0.172714   
Huskers             0.250   1.516410               122      0.219106   
oblivion            0.294   0.915185               177      0.105832   
philosophy          1.119   3.694975               353      0.044773   
Lollapalooza        0.485   1.450440               228      0.255532   
NewOrleans          0.614   3.522642               283      0.140439   
HeroesandGenerals   0.196   0.674970               139      0.125240   
progressive         0.208   0.814086               136      0.055129   
spicy               0.498   1.479188               261      0.144683   
ukulele             0.491   1.759522               216      0.214598   
EA_NHL              0.503   1.808312               218      0.169474   
humor               0.657   1.838845               268      0.083344   
AdvancedRunning     0.283   1.766610               151      0.213102   
PolishGauntlet      0.180   0.584466               140      0.412844   
badtattoos          2.115   4.605624               473      0.328569   
wallpapers          2.158   7.275234               431      0.131337   
OpTicGaming         0.857   2.799741               325      0.206109   
AdoptMyVillager     1.150   3.191160               365      0.360502   
timbers             0.206   0.664503               140      0.202756   
mazda               0.378   1.345034               192      0.135825   
circlejerk          5.619  15.268328               554      0.123857   
SimCity             0.365   1.194895               203      0.116242   
Disney_Infinity     0.346   1.632876               185      0.299049   
pakistan            0.223   0.953557               128      0

In [458]:
ss[ss['aff_wc_in_models'] != 100]

mean         std  slang_to_user_wc  user_percent  \
yorku                 0.126000    1.141106                70      0.105439   
fantasyhockey         0.554000    1.872721               242      0.172103   
SiliconValleyHBO      0.599000    2.062086               246      0.083788   
fresh_funny           0.782609    2.261009                44      0.240000   
Dirtybomb             0.389000    1.294480               196      0.116363   
Fallout4              0.442000    1.438275               215      0.164129   
announcements         1.495000    4.895506               365      0.091465   
mistyfront            0.192000    1.592211                81      0.235583   
Astros                0.363000    1.217058               195      0.225046   
bourbon               4.435345   15.946980               153      0.219309   
Ifyouhadtopickone     1.492201    4.491898               237      0.463152   
Defenders             0.742000    3.941502               253      0.173527   
ayylmao               1.991820    8.845870               221      0.302955   
islam                 4.970223   18.951397               261      0.257059   
homeworld             0.225000    1.067883               129      0.095218   
StarWarsBattlefront   0.891000    2.782287               305      0.140183   
MonarchyOfEquestria   0.012000    0.108885                20      0.226415   
homeland              0.342000    1.450185               158      0.114152   
holidaybullshit       0.382000    1.473796               214      0.109739   
Amateur              13.775000   16.567268                38      0.064384   
collegebaseball       0.367000    1.057502               207      0.318300   
CatsStandingUp       55.000000   51.000000                 2      0.013940   
rocketbeans           0.258000    1.656332               105      0.028065   
OKBestFace            0.108000    0.410288               106      0.542714   
latin                 0.092000    0.394381                79      0.060447   
FreeBits              2.190000   10.028455               655      0.339746   
test                  1.405000   11.315873               407      0.189865   
FantasyMLS            0.112000    0.519092                73      0.165680   
hampan                0.072115    0.258679                16      0.283019   
jerktalkdiamond       0.187000    0.549573               194      0.582555   
...                        ...         ...               ...           ...   
FireflyFestival       0.390000    1.209917               224      0.219842   
monsterhunterclan     1.659000    5.355065               381      0.280711   
FULLCOMMUNISM         0.216000    0.937733               144      0.154728   
NoFapWar              0.450000    1.994868               210      0.316456   
Accounting            5.745763   20.207198               229      0.271961   
ColdWarPowers         0.067000    0.250022                80      0.335000   
KerbalSpaceProgram   20.207018   88.021225               238      0.193489   
orangeisthenewblack   0.742000    2.980509               255      0.127098   
WorldOfWarships       0.551000    1.971649               229      0.130755   
Gundam                3.195767   11.801658               114      0.166667   
TinyLeaders           0.087000    0.339751                80      0.046724   
darkestdungeon        0.392000    1.311616               205      0.114286   
dyinglight            1.507000    4.304178               385      0.150429   
nashville             5.222222   17.697244               100      0.210263   
whatstheword          0.132000    0.585300               101      0.031815   
justified             0.459000    1.743651               234      0.241071   
DWMA                  0.018000    0.132951                21      0.333333   
politota              0.469055    2.158580                67      0.104423   
TechoBlanco           0.087000    0.368010                74      0.199085   
friendsafari         30.113636  124.594168      